# Sales Forecasring

In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import statsmodels.tsa.statespace.sarimax as SARIMAX
import prophet
from sklearn.model_selection import ParameterGrid

c:\Work\upwork timeseries\venv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Importing plotly failed. Interactive plots will not work.


In [3]:
df = pd.read_csv('C:/Users/Ali/Desktop/train_sales_forecast.csv')
future = pd.read_csv('C:/Users/Ali/Desktop/Scoring_Template.csv')

In [4]:
df

Store  Dept        Date  Weekly_Sales  IsHoliday
0          1     1  05-02-2010      25037.08      False
1          1     1  12-02-2010      46247.44       True
2          1     1  19-02-2010      41783.43      False
3          1     1  26-02-2010      19491.18      False
4          1     1  05-03-2010      21926.49      False
...      ...   ...         ...           ...        ...
84051     10    99  03-02-2012        246.11      False
84052     10    99  10-02-2012        517.33       True
84053     10    99  17-02-2012        703.16      False
84054     10    99  02-03-2012         20.09      False
84055     10    99  13-04-2012         20.09      False

[84056 rows x 5 columns]

In [6]:
future['Date'] = pd.to_datetime(future['Date'], format='%d-%m-%Y')
future['IsHoliday'] = future['IsHoliday'].astype(int)

In [7]:
df["Date"] = pd.to_datetime(df["Date"], format='%d-%m-%Y')
df['IsHoliday'] = df['IsHoliday'].astype(int)

### MAPE Calculation Formula

In [9]:
def calculate_mape(actual, predicted):
    # Avoid division by zero
    mask = (actual != 0)
    
    # Calculate absolute percentage error
    absolute_percentage_error = np.abs((actual - predicted) / actual[mask])
    
    # Calculate mean absolute percentage error
    mape = np.mean(absolute_percentage_error) * 100
    
    return mape

### Grid Search for SARIMAX Parameters

In [10]:
def grid_search_sarimax(train_df, test_df, param_grid):
            best_mape = float('inf')
            best_params = None

            for params in list(ParameterGrid(param_grid)):
                try:
                    model = SARIMAX.SARIMAX(train_df['Weekly_Sales'], **params)
                    fit = model.fit()

                    # Forecast for evaluation
                    pred_sales = fit.predict(start=test_df.index[0], end=test_df.index[-1]) 

                    # Evaluate based on MAPE or other metrics
                    mape = calculate_mape(test_df['Weekly_Sales'], pred_sales)

                    if mape < best_mape:
                        best_mape = mape
                        best_params = params
                except:
                    print('Error:', params)
                    continue

            return best_params, best_mape

In [11]:
sarimax_param_grid = {
            'order': [(1, 0, 0), (1, 1, 0), (1, 0, 1), (1, 1, 1), (2, 0, 0), (2, 1, 0), (2, 0, 1), (2, 1, 1)],
            'seasonal_order': [(1, 1, 0, 12), (1, 0, 1, 12), (1, 1, 1, 12), (2, 1, 0, 12), (2, 0, 1, 12), (2, 1, 1, 12), (2, 0, 2, 12)],
        }

### Loop to Train and Predict 

In [16]:
mape_list = []
future_list = []

# for store in df['Store'].unique():
#     for department in df['Dept'].unique():
for i in range(1,11):
    for j in range(1,100):
        temp_df = df[(df['Dept'] == j) & (df['Store'] == i)]
        prophet_df = temp_df.rename(columns={'Date': 'ds', 'Weekly_Sales': 'y'})
        prophet_df = prophet_df.drop(['Store', 'Dept', 'IsHoliday'], axis=1)
        
        prophet_df_train = prophet_df[:-int(len(prophet_df)*0.3)].reset_index(drop=True)
        prophet_df_test = prophet_df[-int(len(prophet_df)*0.3):].reset_index(drop=True)
        
        temp_future = future[(future['Dept'] == j) & (future['Store'] == i)]
        future_prophet = temp_future.rename(columns={'Date': 'ds', 'Weekly_Sales': 'y'})
        future_prophet = future_prophet.drop(['Store', 'Dept', 'IsHoliday'], axis=1)

        temp_holidays = pd.DataFrame({
            'holiday': 'holiday',
            'ds': temp_df[temp_df['IsHoliday'] == 1]['Date']})
        future_holidays = pd.DataFrame({
            'holiday': 'holiday',
            'ds': temp_future[temp_future['IsHoliday'] == 1]['Date']})
        holidays = pd.concat([temp_holidays, future_holidays])
        

        if prophet_df_train.shape[0]>2 and future_prophet.shape[0]>2:
            prophet_model = prophet.Prophet(holidays=holidays, yearly_seasonality=True, weekly_seasonality=False, daily_seasonality=False)
            prophet_fit = prophet_model.fit(prophet_df_train)
            prophet_test = prophet_fit.predict(prophet_df_test)
            
            prophet_mape = calculate_mape(prophet_df_test['y'], prophet_test['yhat'])
            
            
            
        
        
        
        temp_df = temp_df.drop(['Store', 'Dept'], axis=1)
        

        temp_df_train = temp_df[:-int(len(temp_df)*0.3)].reset_index(drop=True)
        temp_df_test = temp_df[-int(len(temp_df)*0.3):].reset_index(drop=True)

        temp_future = temp_future.drop(['Store', 'Dept'], axis=1)
        

        if temp_df_train.shape[0]>2 and temp_future.shape[0]>2:
            best_params, SARIMAX_mape = grid_search_sarimax(temp_df_train, temp_df_test, sarimax_param_grid)

            mape_list.append([i, j, prophet_mape, SARIMAX_mape])

            if SARIMAX_mape < prophet_mape:
                sarimax_model = SARIMAX.SARIMAX(temp_df_train['Weekly_Sales'], order=best_params['order'], seasonal_order=best_params['seasonal_order'])
                sarimax_fit = sarimax_model.fit()
                
                # repeated_exog = np.tile(temp_future['IsHoliday'], len(temp_df_train)//len(temp_future)+1)
                sarimax_future = sarimax_fit.predict(start=temp_future.index[0], end=temp_future.index[-1])
                future_list.append([i, j, sarimax_future])

            else:
                prophet_future = prophet_fit.predict(future_prophet)
                prophet_future = prophet_future['yhat']
                future_list.append([i, j, prophet_future])


        
        
        
        
        

14:22:46 - cmdstanpy - INFO - Chain [1] start processing
14:22:46 - cmdstanpy - INFO - Chain [1] done processing
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\base\model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\base\model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:1009: UserWarning: Non-invertible starting seasonal moving average Using zeros as starting parameters.
  warn('Non-invertible starting seasonal moving average'
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\base\model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnin

Error: {'order': (2, 0, 0), 'seasonal_order': (1, 0, 1, 12)}


c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:978: UserWarning: Non-invertible starting MA parameters found. Using zeros as starting parameters.
  warn('Non-invertible starting MA parameters found.'
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:978: UserWarning: Non-invertible starting MA parameters found. Using zeros as starting parameters.
  warn('Non-invertible starting MA parameters found.'
c:\Wor

Error: {'order': (2, 0, 1), 'seasonal_order': (2, 0, 2, 12)}


c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:978: UserWarning: Non-invertible starting MA parameters found. Using zeros as starting parameters.
  warn('Non-invertible starting MA parameters found.'
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:978: UserWarning: Non-invertible starting MA parameters found. Using zeros as starting parameters.
  warn('Non-invertible starting MA parameters found.'
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
c:\Wor

...

c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:997: UserWarning: Non-stationary starting seasonal autoregressive Using zeros as starting parameters.
  warn('Non-stationary starting seasonal autoregressive'
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\base\model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
c:\Work\u

Error: {'order': (2, 0, 1), 'seasonal_order': (2, 0, 2, 12)}


c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:978: UserWarning: Non-invertible starting MA parameters found. Using zeros as starting parameters.
  warn('Non-invertible starting MA parameters found.'
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:978: UserWarning: Non-invertible starting MA parameters found. Using zeros as starting parameters.
  warn('Non-invertible starting MA parameters found.'
c:\Wor

Error: {'order': (2, 1, 1), 'seasonal_order': (1, 1, 0, 12)}


c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:866: UserWarning: Too few observations to estimate starting parameters for ARMA and trend. All parameters except for variances will be set to zeros.
  warn('Too few observations to estimate starting parameters%s.'
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:866: UserWarning: Too few observations to estimate starting parameters for seasonal ARMA. All parameters except for variances will be set to zeros.
  warn('Too few observations to estimate starting parameters%s.'
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:866: UserWarning: Too few observations to estimate starting parameters for ARMA and trend. All parameters except for variances will be set to zeros.
  warn('Too few observations to estimate starting parameters%s.'
c:\Work\upwork timeseries\venv\Lib\site-packages\statsmodels\tsa\statespace\sarimax.py:866: UserWa

In [179]:
mape_list

[[1, 1, 20.167185207960873, 32.20762718810829],
 [1, 2, 5.0923345596635725, 8.552014488462854],
 [1, 3, 15.00986338495749, 61.490885033983474],
 [1, 4, 5.476241099627602, 8.820206639098648],
 [1, 5, 22.19352208749043, 31.32241422582196],
 [1, 6, 45.35563580168138, 34.258563108516285],
 [1, 7, 35.62843324420099, 41.5799261257795],
 [1, 8, 5.427303635730313, 9.484460771635502],
 [1, 9, 15.413126846097185, 34.53237556356531],
 [1, 10, 11.47174238861341, 11.999921355714456],
 [1, 11, 11.703079219095175, 24.214132748463797],
 [1, 12, 8.850785328867367, 21.77525027891465],
 [1, 13, 7.589905169424773, 7.341870444267684],
 [1, 14, 15.436004329407066, 18.41411158833817],
 [1, 16, 24.645041574375362, 280.42381183506257],
 [1, 17, 12.38407138670289, 25.45576759995422],
 [1, 18, 4956.147529597124, 1365.344092404601],
 [1, 19, 28.44546828450148, 62.707035718095085],
 [1, 20, 26.779362190451362, 26.422981349879986],
 [1, 21, 14.412998031265515, 12.76115016139848],
 [1, 22, 19.17247971775879, 30.0068

In [33]:
len(mape_list)

733

In [45]:
future_list

[[1,
  1,
  0     22537.251767
  1     18249.866885
  2     15016.712367
  3     14276.990002
  4     15513.718330
  5     16640.954495
  6     16279.274629
  7     15136.617881
  8     14833.923572
  9     15748.295627
  10    16612.367580
  11    16255.406485
  12    15112.550303
  13    14544.166921
  14    14978.523440
  15    15445.325923
  16    15130.622139
  17    14752.470591
  18    15419.606347
  19    17971.781210
  20    19808.582449
  21    19985.028088
  22    19928.784884
  23    22548.811860
  24    28464.433408
  25    33999.065496
  Name: yhat, dtype: float64],
 [1,
  2,
  0     45331.894531
  1     45337.629108
  2     45589.310101
  3     45766.325872
  4     45808.803555
  5     45795.509465
  6     45655.313052
  7     45242.183143
  8     44680.128359
  9     44396.379954
  10    44670.072791
  11    45275.158080
  12    45770.614497
  13    46114.706133
  14    46737.661814
  15    47853.219139
  16    48873.166302
  17    48825.077143
  18    44072.295200
  19

In [159]:
target = pd.read_csv('C:/Users/Ali/Desktop/Scoring_Template.csv')

In [88]:
new_list = [row[2].tolist() for row in future_list]

In [86]:
type(future_list[0][2])

pandas.core.series.Series

In [89]:
type(new_list)

list

In [165]:
flatten_list = [item for sublist in new_list for item in sublist]

In [166]:
len(flatten_list)

18569

In [132]:
shape_list = []

In [133]:
for i in range(1,11):
    for j in range(1,100):
        shape = target[(target['Dept'] == j) & (target['Store'] == i)].shape[0]
        if shape > 0:
            shape_list.append([i,j,shape])

In [134]:
target[(target['Dept'] == 1) & (target['Store'] == 1)].shape[0]

26

In [136]:
len(shape_list)

745

In [127]:
sum(shape_list)

18589

In [137]:
list_shape_list =[]

In [138]:
for i in range(len(future_list)):
    list_shape = len(future_list[i][2])
    list_shape_list.append([future_list[i][0],future_list[i][1],list_shape])

In [140]:
len(list_shape_list)

733

In [126]:
sum(list_shape_list)

18569

In [145]:
for i in range (len(list_shape_list)):
    if shape_list[i] not in list_shape_list:
        print(shape_list[i])

[2, 47, 2]
[2, 78, 1]
[4, 47, 2]
[4, 77, 1]
[5, 45, 2]
[6, 47, 2]
[7, 45, 2]
[7, 77, 1]
[8, 77, 3]
[9, 47, 2]
[9, 77, 1]
[10, 45, 1]


In [153]:
old_remove_list = [[2, 47, 2],[2, 78, 1],[4, 47, 2],[4, 77, 1],[5, 45, 2],[6, 47, 2],[7, 45, 2],[7, 77, 1],[8, 77, 3],[9, 47, 2],[9, 77, 1],[10, 45, 1]]
remove_list = []
for i in range(len(old_remove_list)):
    remove_list.append(old_remove_list[i][0:2])

In [161]:
for i in range(1,11):
    for j in range(1,100):
        if [i,j] in remove_list:
            target = target.drop(target.index[(target['Dept'] == j) & (target['Store'] == i)], axis=0)

In [162]:
target.shape

(18569, 5)

In [175]:
target.drop(['Weekly_Sales'], axis=1, inplace=True)

In [176]:
target.insert(4, 'Weekly_Sales', flatten_list)

In [178]:
target.to_csv('C:/Users/Ali/Desktop/Scoring_Template1.csv', index=False)